# 線形回帰
このnoteでは、線形回帰の基本について学んでいきます。
準備用の`python`コードは適宜飛ばして読み進めてください。

In [4]:
# 必要なパッケージのimport
from sklearn import datasets
import pandas as pd
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
import numpy as np
import math
plotly.offline.init_notebook_mode(connected=True) #  notebook上でインタラクティブに操作する設定

In [5]:
# データ読み込み
iris = datasets.load_iris()
#iris.feature_names
# sepal_lengthとpetal_lengthを選択
# iris.feature_names
## ['sepal length (cm)',
##  'sepal width (cm)',
##  'petal length (cm)',
##  'petal width (cm)']
def gen_layout(xtitle, ytitle):
    layout = go.Layout(
        autosize=False,
        width=500,
        height=400,
        showlegend=False,
        xaxis=dict(
            title=xtitle
        ),
        yaxis=dict(
            title=ytitle
        )
    )
    return layout

## データの確認
最初にかなりシンプルな例として、`iris`データを利用します。
- `iris`データは5つのパラメータ(特徴量)を備えていますが、今回はまずそのうち2つのパラメータのみ利用します。
- 後述する`勾配降下法`のため、**各パラメータは平均0、分散1で正規化**しておきます。

In [6]:
x_index = 0
y_index = 2

# 平均0、分散1で正規化
def scale(arr):
    m = np.mean(arr)
    s = np.var(arr)
    return (arr - m)/s

traces = [
    go.Scatter(
        x = scale(iris.data[:,x_index]),
        y = scale(iris.data[:,y_index]),
        mode = "markers" # for scatter plot?
    )
]

# データ概要プロット
layout = gen_layout(iris.feature_names[x_index], iris.feature_names[y_index])
fig = go.Figure(data=traces, layout=layout)
plotly.offline.iplot(fig)

## 用語
先に、これから出てくる用語の説明をしておきます。

### 目的変数
- 求めたい値(基本形だと1つのパラメータ)

### 説明変数
- `目的変数`を決める(1つ以上のパラメータ)

## 回帰
- 1つ以上の説明変数から、目的変数を求める

### 線形回帰

`目的変数`を求めるのに、1つ**以上**の`説明変数`(×係数)の和で求められるような回帰を、特に`線形回帰`と呼びます。
単純な例として、ただ1つの変数で値が求まるようなデータがあったとした時、
$y$ を目的変数、$x$ を説明変数として

$$
\hat{y}= a x + b
$$ でデータを表現します。

- $y$ でなく $\hat{y}$ と表現しているのは、これが真のデータ(観察結果)ではなく、回帰結果であることを示すためです。後で、$y$と$\hat{y}$の違いを考えたりするときに、こう表現しておくと便利です。この記法はデファクトスタンダードとまでは言えないかもしれませんが、良く見かけます。

より、一般的には、以下のような数式で表せます。($n$ は説明変数の数)

$$
\hat{y} = a_0 + a_1x_1 + a_2x_2 + \dots + a_nx_x = \sum_{i=0}^na_ix_i
$$

- $a_0$はさっきの$b$に相当。$x_0 = 1$

- $a$ は $w$(weight: 重み)や $\theta$(由来不明) と書くこともあります。

上式は、行列表現を用いると、$\mathbf{a} = (a_1, a_2, \dots, a_n)$, $\mathbf{x} = (x_1, x_2, \dots, x_n)$ として

$$
\hat{y} = \mathbf{a}^\mathrm{T}\mathbf{x} + b
$$

と表すことも出来ます。

## 線形回帰の例
では、先程の2次元プロットしたグラフに、適当な回帰線を引いてみましょう。
上式で

- $a = 0$
- $b = 0$

とした時の回帰線は、以下のようになります。

In [7]:
def fx(x, a, b):
    y = a * x + b
    return y

x = np.arange(-3,5)
y = fx(x, 0, 0)
    
traces2 = [
    traces[0]
    ,
    go.Scatter(
        x = x,
        y = y,
        mode = "lines"
    )
]

fig2 = go.Figure(data=traces2, layout=layout)
plotly.offline.iplot(fig2)

どうでしょう。この回帰線は、実際のデータをうまく表現できているでしょうか。
なんとなく、もっと上手な直線を引けるように見えますね。

では、どういう回帰線が、データを上手く表現していると言えるでしょうか。

## 損失関数
回帰によって、$\hat{y}$ が求まった時、実際のデータ$y$ との違い、もっと言えば、$y$が持っていた値から欠け落ちた部分を`損失(Loss)`と呼びます。良い回帰とは、この損失が最も小さくなるような回帰になります。

線形回帰(もっと広く、線形モデル)では、特に$y$と$\hat{y}$の`2乗誤差`の平均を損失関数とします。

データの標本数(データ数)を$m$、損失関数を$L(\hat{y},y)$と表現すると

$$
L(\hat{y}, y) = \frac{\sum_{i=0}^{m}(y - \hat{y})^2}{2m}
$$

と表します。

- 本来、分母は$m$ ですが、計算を簡単にする都合で、$2m$としています。(微分するときに便利)

さて、この損失関数が最小になるとき、その回帰結果は最も良いと言えそうです。損失関数が最小となるのは、損失関数が下に凸で、その微分が0になるときです。(最小になるような場合を求めたいだけなので、先程分母を2倍した事が結果に影響することはありません。)


## 勾配降下法

損失関数は、説明変数がn個の時、n+1次元($a_0$: 定数項で+1)で表現されます。
これを簡易的に3次元プロットする($a_0,a_1,a_2$へのプロット)と、以下のような曲面になります。

![](http://charlesfranzen.com/images/gradient.png)
- 引用元: http://charlesfranzen.com/posts/multiple-regression-in-python-gradient-descent/

こういう曲面に対して、漸近的に値が小さくなるようにパラメータを変化させていって、最終的に曲面の凸部分(損失関数の最小値)を得る方法を`勾配降下法`といいます。

- 損失関数が単峰でなく、複数の凸部分がある場合、最も低い箇所に到達できないことがあります。(部分最適解になります。)
  - 開始点(初期の$\mathbf{a}$)に依存。何度か試せば良い。
 
以降では、

- 説明変数の数$n$ ($i$がインデックス指定用)
- 標本の数$m$ ($j$がインデックス指定用)

として、具体的に勾配降下法を用いた計算手順を説明します。

$\hat{y} = \sum_{j=1}^{n}a_ix_i = h_a(\mathbf{x})$ とすると、上の損失関数は、次のように表せます。

$$
L(\hat{y}, y) = \frac{1}{2m}\sum_{i=1}^{m}(h_a(\mathbf{x}^{(i)}) - \mathbf{y}^{(i)})^2
$$

- $\mathbf{x}^{(i)}$ は$i$番目の標本での$\mathbf{x}$

これを各パラメータの回帰係数 $a_j$ごとに偏微分すると

$$
\frac{\partial{L}}{\partial{a_j}} = \frac{1}{m}\left(\sum_{i=1}^{m}(h_a(\mathbf{x}^{(i)}) - \mathbf{y}^{(i)})\right)x_j^{(i)}
$$

となります。この偏微分値を用いて、回帰係数$\mathbf{a}$を更新していきます。

$$
a_i := a_i - \alpha\frac{\partial{L}}{\partial{a_j}}
$$

- $\alpha$は`学習率`と呼ばれるハイパーパラメータで、良さげな値を回帰実行者が決める必要があります。
  - 小さくすると、最小値が求まるまでにより多くのループ回数が必要な代わりにきちんと少しずつ小さい値をとります。
  - 大きくすると、ループ回数は少なくすみますが、大きすぎる場合には最小値付近で損失関数が増減してしまいます。(収束しにくくなります。)
- 全ての$a_0,...,a_n$を更新するまで、$\frac{\partial{L}}{\partial{a_j}}$内の$a_0,...,a_n$は前のループでの結果を使います。
  - あるループ内で、$a_0$を更新した後、$\frac{\partial{L}}{\partial{a_1}}$を計算する際の$a_0$は更新前の値を用います。


### 注意点

- 勾配降下法では各次元(各パラメータ)が同じような範囲に収まっている必要があります。
  - 平均0、分散1で正規化するのが簡単だが、他の方法でも良い。
  - 次元ごとに桁が違うような場合、分布がどこかの次元に対して狭くなり、損失が単純降下しづらくなる。

---
尚、ここでは扱いませんが、別の解法として、上の損失関数の対数をとって、正規方程式という形に落とし込む手法もあります。






In [8]:
# 損失関数の計算
def calc_L(X, Y, A):
    m = X.shape[1]
    #X_ = np.array((X, np.ones(m))) # x_0の追加
    h = np.dot(A.T, X)
    return 1/m*np.sum((h - Y)**2)

# 偏相関の計算
def calc_partial_L(X, Y, A):
    m = X.shape[1]
    #X_ = np.array((X, np.ones(m)))
    h = np.dot(A.T, X)
    return 1/m*np.sum((h - Y)*X, axis=1)

# 回帰係数の更新
def update_A(A, p, leaning_rate):
    return A - p*learning_rate

### 損失関数のプロット

イメージをつかむために、

- 損失関数の等高線
- 損失関数の3次元プロット

を見ておきましょう。

In [9]:
xrange = np.arange(-3.0, 3.0, 0.05)
yrange = np.arange(-3.0, 3.0, 0.05)

# 観測データの説明変数 (2,m)行列
X = scale(iris.data[:,x_index])
X = np.array((np.ones(X.shape[0]), X))
# 観測データの目的変数 (1,m)行列
Y = scale(iris.data[:,y_index])

c = np.array([(x, y) for x in xrange for y in yrange])
cn = c.shape[0]
contourdata = np.zeros((cn,3))
for row in range(1, c.shape[0]):
    a = c[row,:]
    tmp = np.append(a, calc_L(X, Y, a))
    contourdata[row,:] = tmp

data_contour = go.Contour(
    z = contourdata[:,2],
    x = contourdata[:,0],
    y = contourdata[:,1],
    contours=dict(
        coloring='heatmap'
    )
)

layout_contour = gen_layout('a0','a1')
fig_contour = go.Figure(data=[data_contour], layout=layout_contour)
plotly.offline.iplot(fig_contour)

In [10]:
size = math.floor(np.sqrt(contourdata[:,2].shape)[0])
contourmat = contourdata[:,2].reshape((size,size))

data_contour3d = go.Surface(
    z = contourmat,
    x = xrange,
    y = yrange
)
layout_contour3d = go.Layout(
    title='Loss',
    autosize=True,
    width=500,
    height=500,
    margin=dict(
        l=65,
        r=50,
        b=65,
        t=90
    )
)
fig_contour3d = go.Figure(data=[data_contour3d], layout=layout_contour3d)
plotly.offline.iplot(fig_contour3d)

### 実際に勾配降下法を試す

理解も深まったと思いますので、実際に先程のデータに対して勾配降下法を行い、
最適な回帰係数を求めてみます。

In [15]:
# 学習率
learning_rate = 0.05
# ループ回数
loop = 100

# 回帰係数(求めたい結果) (2,1)行列
# 初期値は、後に出てくる等高線での開始点になります。
A = np.array([-3,-3])#np.zeros(2) # 各回帰係数を0で初期化

## 上の方で定義してあるけど、説明のため再掲。
# 観測データの説明変数 (2,m)行列
X = scale(iris.data[:,x_index])
X = np.array((np.ones(X.shape[0]), X))
# 観測データの目的変数 (1,m)行列
Y = scale(iris.data[:,y_index])

ls = np.zeros(loop)     # 描画用に損失関数の推移を保存しておく
As = np.zeros((loop,2)) # 描画用に回帰係数の推移を保存しておく
idx = np.zeros(loop)    # 描画用にループ回数を保存しておく
# 一定回数ループ処理をする。
# 実際には、損失関数の差が小さくなったら処理を止めても良い。
for i in range(0,loop):
  # 損失関数を求める
  l = calc_L(X,Y,A)
  # 損失関数の回帰係数に対する偏微分を求める(回帰係数ごと) 
  p = calc_partial_L(X,Y,A)
  # 回帰係数を更新する
  A = update_A(A, p, learning_rate)
  # 後で使う描画用の値を格納
  ls[i] = l
  idx[i] = i
  As[i,:] = A

print("回帰結果: y = ", A[1], "x + ", A[0])
print("最終損失: L = ", l)

回帰結果: y =  0.407460626056 x +  -0.017761587661
最終損失: L =  0.0779777479077


### 勾配降下法での推移を観察
勾配降下法で、ループ毎に回帰係数$a_0$、$a_1$がどのように変化していくかを
先程の等高線にプロットしてみます。

学習率が適切なら、きちんと等高線の最小部の中央付近に収束していることが確認できます。

In [12]:
data_contour2 = [
    data_contour,
    go.Scatter(
        x = As[:,0],
        y = As[:,1],
        mode = "lines"
    )
]
fig_contour2 = go.Figure(data=data_contour2, layout=layout_contour)
plotly.offline.iplot(fig_contour2)

また、損失の推移も確認しておきましょう。
学習率が適切でない場合には、単純な減衰曲線にはならないため、こうしたプロットが適切な学習率を得る手助けになります。

In [13]:
traces_loss = [
  go.Scatter(
      x = idx,
      y = ls,
      mode = "lines"
  )
]
layout_loss = gen_layout("イテレーション回数", "損失")
fig_loss = go.Figure(data = traces_loss, layout = layout_loss)
plotly.offline.iplot(fig_loss)

## 回帰曲線の表示

ここまでで、線形回帰を用いて、回帰線を得ることができました。
元のグラフにプロットし、うまくいったか確認しましょう。

In [14]:
y = fx(x, A[1], A[0])
traces3 = [
    traces[0]
    ,
    go.Scatter(
        x = x,
        y = y,
        mode = "lines"
    )
]

fig3 = go.Figure(data=traces3, layout=layout)
plotly.offline.iplot(fig3)

## まとめ
いかがでしたでしょうか。
今回は機械学習の初歩として、その基礎をなす線形回帰を取り扱いました。

線形回帰を理解することは、
次に扱う正則化付き線形回帰、そしてニューラルネットの基礎をなすロジスティック回帰を学ぶ大きな手助けになるでしょう。

## 参考資料

[The Iris Dataset — scikit-learn 0.19.0 documentation](http://scikit-learn.org/stable/auto_examples/datasets/plot_iris_dataset.html)
- `scikit-learn`にいくつかサンプル用データセットがあるので、利用。
